In [1]:
import numpy as np
from datetime import datetime
def numerical_derivative(f,x):
    
    it = np.nditer(x, flags=['multi_index'], op_flags=['readwrite'])
    delta = 1e-5
    grad = np.zeros_like(x)
    
    while not it.finished:
        idx = it.multi_index
        tmp_val = x[idx]
        
        x[idx] = float(tmp_val)+delta
        fx1 = f(x)
        
        x[idx] = tmp_val-delta
        fx2 = f(x)
        
        grad[idx] = (fx1-fx2)/(2*delta)
        
        x[idx] = tmp_val
        it.iternext()
        
    return grad
    

In [2]:
class Diabetes:
    def __init__(self, name, xdata, tdata, i_node, h1_node, o_node, lr, iter_count):
        
        if xdata.ndim == 1:
            raise Exception("<__init__> vector is not permissioned")
        
        # save parameter
        self.name = name
        
        self.xdata = xdata
        self.tdata = tdata
        
        self.i_node = i_node
        self.h1_node = h1_node
        self.o_node = o_node
        
        self.lr = lr
        self.iter_count = iter_count
        
        # assign W,b
        self.W2 = np.random.randn(i_node, h1_node)
        self.b2 = np.random.randn(h1_node)
        
        self.W3 = np.random.randn(h1_node, o_node)
        self.b3 = np.random.randn(o_node)
        
        print("class is created")
        
    def sigmoid(self, x):
        return 1/(1+np.exp(-x))
    
    def feed_forward_solo_data(self, xdata, tdata):
        
        y = self.feed_forward_cal(xdata)      
        return -np.sum(tdata*np.log(y+1e-7)+(1-tdata)*np.log((1-y)+1e-7))
    
    def feed_forward_multiple_data(self):
        y = self.feed_forward_cal(self.xdata)
        return -np.sum(self.tdata*np.log(y+1e-7)+(1-self.tdata)*np.log((1-y)+1e-7))
    
    def feed_forward_cal(self, xdata):
        
        Z2 = np.dot(xdata, self.W2)+ self.b2
        A2 = self.sigmoid(Z2)
        
        Z3 = np.dot(A2, self.W3) + self.b3
        y = A3 = self.sigmoid(Z3)
        
        return y
    
    def accuracy(self, test_x_data, test_t_data):
        
        if test_x_data.ndim != 2:
            raise Exception("<accuracy> only matrix can be used")
        
        matched_list = []
        not_matched_list = []
        
        for i in range(len(test_x_data)):
            y,predict_res = self.predict(test_x_data[i])
            
            if predict_res == test_t_data[i]:
                matched_list.append(test_x_data[i])
            else:
                not_matched_list.append(test_x_data[i])
        
        accuracy_val = len(matched_list) / len(test_x_data)
        
        return accuracy_val, matched_list, not_matched_list
            
    def predict(self, test_x_data):
        
        if test_x_data.ndim != 1:
            raise Exception("<predict> only vector can be used")
        
        y = self.feed_forward_cal(test_x_data)
        
        if y >= 0.5 :
            return (y,1)
        else:
            return (y,0)
      
    def train(self):
        start = datetime.now()
        
#         print("start  loss: ",self.feed_forward_multiple_data())
        
        for i in range(self.iter_count):
            
            print("---------------------------------------------")
            print("step ",i,"loss: ",self.feed_forward_multiple_data())
            print("---------------------------------------------")
            for j, (xdata, tdata) in enumerate(zip(self.xdata, self.tdata)):
                
               
                f = lambda x : self.feed_forward_solo_data(xdata, tdata)
            
                self.W2 -= numerical_derivative(f, self.W2) * self.lr
                self.b2 -= numerical_derivative(f, self.b2) * self.lr

                self.W3 -= numerical_derivative(f, self.W3) * self.lr
                self.b3 -= numerical_derivative(f, self.b3) * self.lr
                
                
                if j % 200 == 0 : 
                    
                    print("j:", j,  xdata, tdata,"loss: ", self.feed_forward_solo_data(xdata, tdata))
                    

        print("final loss: ",self.feed_forward_multiple_data())
                
        end = datetime.now()
    
        print("elapsed time => ",end-start)

In [3]:
data = np.genfromtxt('diabetes.csv',delimiter=',')
print(data)

[[-0.294118   0.487437   0.180328  ... -0.53117   -0.0333333  0.       ]
 [-0.882353  -0.145729   0.0819672 ... -0.766866  -0.666667   1.       ]
 [-0.0588235  0.839196   0.0491803 ... -0.492741  -0.633333   0.       ]
 ...
 [-0.411765   0.21608    0.180328  ... -0.857387  -0.7        1.       ]
 [-0.882353   0.266332  -0.0163934 ... -0.768574  -0.133333   0.       ]
 [-0.882353  -0.0653266  0.147541  ... -0.797609  -0.933333   1.       ]]


In [4]:
test_cnt = 200
xdata = data[:-test_cnt,:-1]
tdata = data[:-test_cnt,-1:]

print("xdata.shape",xdata.shape)
print("tdata.shape",tdata.shape)

test_xdata = data[-test_cnt:, :-1]
test_tdata = data[-test_cnt:, -1:]

xdata.shape (559, 8)
tdata.shape (559, 1)


In [6]:
i_node = 8
h1_node = 30
o_node = 1
lr = 0.01
iter_count = 50

obj = Diabetes("Diabetes", xdata,tdata, i_node, h1_node, o_node, lr, iter_count)
obj.train()

class is created
---------------------------------------------
step  0 loss:  405.9039913117267
---------------------------------------------
j: 0 [-0.294118    0.487437    0.180328   -0.292929    0.          0.00149028
 -0.53117    -0.0333333 ] [0.] loss:  1.725469072342886
j: 200 [ 0.         0.0854271  0.114754  -0.59596    0.        -0.186289
 -0.394535  -0.633333 ] [1.] loss:  0.7279047608101711
j: 400 [-0.529412  0.155779  0.180328  0.        0.       -0.138599 -0.745517
 -0.166667] [0.] loss:  0.8812159870780633
---------------------------------------------
step  1 loss:  319.81424872751063
---------------------------------------------
j: 0 [-0.294118    0.487437    0.180328   -0.292929    0.          0.00149028
 -0.53117    -0.0333333 ] [0.] loss:  0.986441492169013
j: 200 [ 0.         0.0854271  0.114754  -0.59596    0.        -0.186289
 -0.394535  -0.633333 ] [1.] loss:  0.7031569750634149
j: 400 [-0.529412  0.155779  0.180328  0.        0.       -0.138599 -0.745517
 -0.16666

j: 200 [ 0.         0.0854271  0.114754  -0.59596    0.        -0.186289
 -0.394535  -0.633333 ] [1.] loss:  0.44354543855480333
j: 400 [-0.529412  0.155779  0.180328  0.        0.       -0.138599 -0.745517
 -0.166667] [0.] loss:  1.197863758711217
---------------------------------------------
step  17 loss:  273.6303176306541
---------------------------------------------
j: 0 [-0.294118    0.487437    0.180328   -0.292929    0.          0.00149028
 -0.53117    -0.0333333 ] [0.] loss:  0.6404343011975095
j: 200 [ 0.         0.0854271  0.114754  -0.59596    0.        -0.186289
 -0.394535  -0.633333 ] [1.] loss:  0.4392276589580118
j: 400 [-0.529412  0.155779  0.180328  0.        0.       -0.138599 -0.745517
 -0.166667] [0.] loss:  1.1996455021153989
---------------------------------------------
step  18 loss:  273.35473898482405
---------------------------------------------
j: 0 [-0.294118    0.487437    0.180328   -0.292929    0.          0.00149028
 -0.53117    -0.0333333 ] [0.] loss:

j: 400 [-0.529412  0.155779  0.180328  0.        0.       -0.138599 -0.745517
 -0.166667] [0.] loss:  1.1947288538224448
---------------------------------------------
step  33 loss:  270.2919533936704
---------------------------------------------
j: 0 [-0.294118    0.487437    0.180328   -0.292929    0.          0.00149028
 -0.53117    -0.0333333 ] [0.] loss:  0.6076303645343966
j: 200 [ 0.         0.0854271  0.114754  -0.59596    0.        -0.186289
 -0.394535  -0.633333 ] [1.] loss:  0.42346764399620984
j: 400 [-0.529412  0.155779  0.180328  0.        0.       -0.138599 -0.745517
 -0.166667] [0.] loss:  1.1936126218445409
---------------------------------------------
step  34 loss:  270.12316587721443
---------------------------------------------
j: 0 [-0.294118    0.487437    0.180328   -0.292929    0.          0.00149028
 -0.53117    -0.0333333 ] [0.] loss:  0.6056952823898778
j: 200 [ 0.         0.0854271  0.114754  -0.59596    0.        -0.186289
 -0.394535  -0.633333 ] [1.] loss

---------------------------------------------
step  49 loss:  267.8120686918767
---------------------------------------------
j: 0 [-0.294118    0.487437    0.180328   -0.292929    0.          0.00149028
 -0.53117    -0.0333333 ] [0.] loss:  0.5785925966183921
j: 200 [ 0.         0.0854271  0.114754  -0.59596    0.        -0.186289
 -0.394535  -0.633333 ] [1.] loss:  0.44015401660146547
j: 400 [-0.529412  0.155779  0.180328  0.        0.       -0.138599 -0.745517
 -0.166667] [0.] loss:  1.1725068640502074
final loss:  267.66875090829484
elapsed time =>  0:04:26.857999


In [ ]:
accuracy, matched_list, not_matched_list = obj.accuracy(test_xdata,test_tdata)

In [8]:
print(accuracy)

0.705
